# Find the 'betweenness' of the edge of the street network which the sensor is closest to

NB: Need to use footfall_spatial environment to run this script!

In [31]:
import geopandas as gpd
import pandas as pd
from shapely.errors import ShapelyDeprecationWarning
import warnings
warnings.filterwarnings("ignore", category=ShapelyDeprecationWarning) 
from shapely.geometry import Point, LineString
import folium
from folium import Map, FeatureGroup, LayerControl

# Function which converts the geometry column in the gpd of edges into the required format
def get_coords(frame):
    xy = frame.geometry.xy
    longs = xy[0].tolist()
    lats = xy[1].tolist()
    return [list(z) for z in zip(lats, longs)]

def create_features_gdf (fp):
    # Read in csv
    feature_df = pd.read_csv(fp)
    # Convert to geodataframe
    feature_gdf = gpd.GeoDataFrame(feature_df, geometry=gpd.points_from_xy(feature_df['Longitude'], feature_df['Latitude']))
    feature_gdf.set_crs(epsg=4326, inplace=True)
    
    return feature_gdf

### Read in sensor data

In [78]:
sensors_gdf = create_features_gdf('../Data/melbourne_locations.csv')

### Read in the edge data and convert format

In [3]:
gdf_edges = gpd.read_file("../Data/gdf_edges/gdf_edges.shp")
gdf_edges['coords'] = gdf_edges.apply(get_coords, axis=1)

###  Join with extra info

In [4]:
network = gpd.read_file("../Data/network/network.shp")
# network['coords'] = network.apply(get_coords, axis=1)
merged = gdf_edges.merge(network, on = 'geometry', how = 'left')
# print(len(network))
# print(len(gdf_edges))
# print(len(merged))
# merged.plot(column='betweenn_1', figsize =(10,10), scheme = 'EqualInterval', legend = True)

In [56]:
private_connections = merged[merged['TRAFFIC']=='Private Connection']
not_private_connections = merged[merged['TRAFFIC']!='Private Connection']

### Plot all the edges and sensors

In [5]:
# # Plot
# melbourne_map = folium.Map(location=[sensors_gdf.Latitude.mean(),
#                            sensors_gdf.Longitude.mean()], zoom_start=13, control_scale=True)
# for index, location_info in sensors_gdf.iterrows():
#     folium.Marker([location_info["Latitude"], location_info["Longitude"]], popup=location_info["sensor_id"]).add_to(melbourne_map)
# folium.PolyLine(locations = gdf_edges['coords'], color="red", weight=1, opacity=1).add_to(melbourne_map)    
# melbourne_map

### Find the edge which is closest to each sensor
(Plot the first 3 to sense check)

In [74]:
closest_edges = merged.iloc[min_dist_idx_ls]

In [63]:
betweenness = []
min_dist_idx_ls = []
# Loop through all of the sensors
for index, location_info in sensors_gdf.iterrows():
    # Get one location of a sensor
    point = Point(location_info['Longitude'],location_info['Latitude'])
    
    # Loop through all the edges and check their distance to the location of this sensor
    # Create an initial dummy min_dist which is stupidly high 
    min_dist = 100
    for i in range(0,len(merged['geometry'])):
        line = merged['geometry'][i]
        if line.distance(point)< min_dist and merged['TRAFFIC'][i] != 'Private Connection':
            min_dist= line.distance(point)
            min_dist_idx = i
    # Add the betweenness from the edge which is the minimum distance from the sensor to a list        
    betweenness.append(gdf_edges['betweenn_1'][min_dist_idx])
    min_dist_idx_ls.append(min_dist_idx)
#     # Plot for first 3 to check
#     if location_info['sensor_id'] in [47,48,49,50,51]:       
#         # Plot the closest street           
#         f = folium.Figure(width=500, height=500)
#         melbourne_map = folium.Map(location=[location_info.Latitude,location_info.Longitude], zoom_start=17, control_scale=True, min_zoom = 13).add_to(f)
#         folium.Marker([location_info["Latitude"], location_info["Longitude"]], popup=location_info["sensor_id"]).add_to(melbourne_map)
#         folium.PolyLine(locations = merged['coords'], color="black", weight=1, opacity=0.7).add_to(melbourne_map)    
#         folium.PolyLine(locations = merged['coords'][min_dist_idx], color="red", weight=10, opacity=1).add_to(melbourne_map)    
#         display(melbourne_map) 

In [85]:
location_info = sensors_gdf.iloc[0]
# Get one location of a sensor
point = Point(location_info['Longitude'],location_info['Latitude'])

# Loop through all the edges and check their distance to the location of this sensor
# Create an initial dummy min_dist which is stupidly high 
min_dist = 100
for i in range(0,len(merged['geometry'])):
    line = merged['geometry'][i]
    if line.distance(point)< min_dist and merged['TRAFFIC'][i] != 'Private Connection':
        min_dist= line.distance(point)
        min_dist_idx = i
# Add the betweenness from the edge which is the minimum distance from the sensor to a list        
betweenness.append(gdf_edges['betweenn_1'][min_dist_idx])

# Plot the basic map        
f = folium.Figure(width=800, height=600)
melbourne_map = folium.Map(location=[location_info.Latitude,location_info.Longitude], zoom_start=15, 
                           control_scale=True).add_to(f)

# Add sensors
sensors_fg=folium.FeatureGroup(name='Sensors', show=False)
melbourne_map.add_child(sensors_fg)
for index, location_info in sensors_gdf.iterrows():
    folium.Marker([location_info["Latitude"], location_info["Longitude"]], radius=5,
                  popup = location_info['sensor_description']).add_to(sensors_fg)   

# Add private connections
private_connections_fg=folium.FeatureGroup(name='Private Connections', show=False)
melbourne_map.add_child(private_connections_fg)
private_connections_cluster = folium.PolyLine(locations = private_connections['coords'], color="red", weight=3, opacity=1).add_to(private_connections_fg)

# Add nonprivate connections
nonprivate_connections_fg=folium.FeatureGroup(name='Non Private Connections', show=False)
melbourne_map.add_child(nonprivate_connections_fg)
nonprivate_connections_cluster = folium.PolyLine(locations = not_private_connections['coords'], color="purple", weight=3, opacity=1).add_to(nonprivate_connections_fg)

# Add closest edges
closest_edges_fg=folium.FeatureGroup(name='Closest edges', show=False)
melbourne_map.add_child(closest_edges_fg)
closest_edges_cluster = folium.PolyLine(locations = closest_edges['coords'], color="green", weight=3, opacity=1).add_to(closest_edges_fg)

# Add layer control
melbourne_map.add_child(LayerControl("topright", collapsed = False))
display(melbourne_map)

### Join to the dataframe containing the number of features near each sensor

In [ ]:
betweenness_df = pd.DataFrame({'sensor_id': sensors_gdf['sensor_id'], "betweenness": betweenness})

In [ ]:
betweenness_df = betweenness_df.sort_values(by='sensor_id', ascending = True)

### Save to file

In [100]:
betweenness_df.to_csv("../Cleaned_data/sensors_betweenness.csv", index = False)